In [ ]:
import os
from sys import stdout
from tqdm import tqdm
from timeit import default_timer as timer

os.environ["OMP_NUM_THREADS"] = "1"  # export OMP_NUM_THREADS=4
os.environ["OPENBLAS_NUM_THREADS"] = "1"  # export OPENBLAS_NUM_THREADS=4
os.environ["MKL_NUM_THREADS"] = "1"  # export MKL_NUM_THREADS=6
os.environ["VECLIB_MAXIMUM_THREADS"] = "1"  # export VECLIB_MAXIMUM_THREADS=4
os.environ["NUMEXPR_NUM_THREADS"] = "1"  # export NUMEXPR_NUM_THREADS=6

import numpy as np
import sisl
from src.grogu_magn.useful import *
from mpi4py import MPI
from numpy.linalg import inv
import warnings

# runtime information
times = dict()
times["start_time"] = timer()

In [ ]:
# this cell mimicks an input file
fdf = sisl.get_sile("./Jij_for_Marci_6p45ang/CrBr.fdf")  # ./lat3_791/Fe3GeTe2.fdf
# this information needs to be given at the input!!
scf_xcf_orientation = np.array([0, 0, 1])  # z
# list of reference directions for around which we calculate the derivatives
# o is the quantization axis, v and w are two axes perpendicular to it
# at this moment the user has to supply o,v,w on the input.
# we can have some default for this
ref_xcf_orientations = [
    dict(o=np.array([1, 0, 0]), vw=[np.array([0, 1, 0]), np.array([0, 0, 1])]),
    dict(o=np.array([0, 1, 0]), vw=[np.array([1, 0, 0]), np.array([0, 0, 1])]),
    dict(o=np.array([0, 0, 1]), vw=[np.array([1, 0, 0]), np.array([0, 1, 0])]),
]

"""
# human readable definition of magnetic entities ./lat3_791/Fe3GeTe2.fdf
magnetic_entities = [
    dict(atom=3, l=2),
    dict(atom=4, l=2),
    dict(atom=5, l=2),
    dict(
        atom=[3, 4],
    ),
]
# pair information ./lat3_791/Fe3GeTe2.fdf
pairs = [
    dict(ai=0, aj=1, Ruc=np.array([0, 0, 0])),  # isotropic should be -82 meV
    dict(
        ai=0, aj=2, Ruc=np.array([0, 0, 0])
    ),  # these should all be around -41.9 in the isotropic part
    dict(ai=1, aj=2, Ruc=np.array([0, 0, 0])),
    dict(ai=0, aj=2, Ruc=np.array([-1, 0, 0])),
    dict(ai=1, aj=2, Ruc=np.array([-1, 0, 0])),
] """

# human readable definition of magnetic entities ./Jij_for_Marci_6p45ang/CrBr.fdf
magnetic_entities = [
    dict(atom=0, l=2),
    dict(atom=1, l=2),
    dict(atom=2, l=2),
]
# pair information ./Jij_for_Marci_6p45ang/CrBr.fdf
pairs = [
    dict(ai=0, aj=1, Ruc=np.array([0, 0, 0])),
    dict(ai=0, aj=2, Ruc=np.array([0, 0, 0])),
    dict(ai=1, aj=2, Ruc=np.array([0, 0, 0])),
    dict(ai=0, aj=1, Ruc=np.array([1, 0, 0])),
    dict(ai=0, aj=2, Ruc=np.array([1, 0, 0])),
    dict(ai=0, aj=1, Ruc=np.array([-1, 0, 0])),
    dict(ai=0, aj=2, Ruc=np.array([-1, 0, 0])),
    dict(ai=0, aj=1, Ruc=np.array([0, 1, 0])),
    dict(ai=0, aj=2, Ruc=np.array([0, 1, 0])),
    dict(ai=0, aj=1, Ruc=np.array([0, 1, 0])),
    dict(ai=0, aj=2, Ruc=np.array([0, 1, 0])),
]


# Brilloun zone sampling and Green function contour integral
kset = 20
kdirs = "xy"
ebot = -30
eset = 100
esetp = 10000


# MPI parameters
comm = MPI.COMM_WORLD
size = comm.Get_size()
rank = comm.Get_rank()
root_node = 0
if rank == root_node:
    print("Number of nodes in the parallel cluster: ", size)

simulation_parameters = dict(
    path="Not yet specified.",
    scf_xcf_orientation=scf_xcf_orientation,
    ref_xcf_orientations=ref_xcf_orientations,
    kset=kset,
    kdirs=kdirs,
    ebot=ebot,
    eset=eset,
    esetp=esetp,
    parallel_size=size,
)

# digestion of the input
# read in hamiltonian
dh = fdf.read_hamiltonian()
try:
    simulation_parameters["geom"] = fdf.read_geometry()
except:
    print("Error reading geometry.")

# unit cell index
uc_in_sc_idx = dh.lattice.sc_index([0, 0, 0])

times["setup_time"] = timer()

In [ ]:
NO = dh.no  # shorthand for number of orbitals in the unit cell

# preprocessing Hamiltonian and overlap matrix elements
h11 = dh.tocsr(dh.M11r)
h11 += dh.tocsr(dh.M11i) * 1.0j
h11 = h11.toarray().reshape(NO, dh.n_s, NO).transpose(0, 2, 1).astype("complex128")

h22 = dh.tocsr(dh.M22r)
h22 += dh.tocsr(dh.M22i) * 1.0j
h22 = h22.toarray().reshape(NO, dh.n_s, NO).transpose(0, 2, 1).astype("complex128")

h12 = dh.tocsr(dh.M12r)
h12 += dh.tocsr(dh.M12i) * 1.0j
h12 = h12.toarray().reshape(NO, dh.n_s, NO).transpose(0, 2, 1).astype("complex128")

h21 = dh.tocsr(dh.M21r)
h21 += dh.tocsr(dh.M21i) * 1.0j
h21 = h21.toarray().reshape(NO, dh.n_s, NO).transpose(0, 2, 1).astype("complex128")

sov = (
    dh.tocsr(dh.S_idx)
    .toarray()
    .reshape(NO, dh.n_s, NO)
    .transpose(0, 2, 1)
    .astype("complex128")
)


# Reorganization of Hamiltonian and overlap matrix elements to SPIN BOX representation
U = np.vstack(
    [np.kron(np.eye(NO, dtype=int), [1, 0]), np.kron(np.eye(NO, dtype=int), [0, 1])]
)
# This is the permutation that transforms ud1ud2 to u12d12
# That is this transforms FROM SPIN BOX to ORBITAL BOX => U
# the inverse transformation is U.T u12d12 to ud1ud2
# That is FROM ORBITAL BOX to SPIN BOX => U.T

# From now on everything is in SPIN BOX!!
hh, ss = np.array(
    [
        U.T @ np.block([[h11[:, :, i], h12[:, :, i]], [h21[:, :, i], h22[:, :, i]]]) @ U
        for i in range(dh.lattice.nsc.prod())
    ]
), np.array(
    [
        U.T
        @ np.block([[sov[:, :, i], sov[:, :, i] * 0], [sov[:, :, i] * 0, sov[:, :, i]]])
        @ U
        for i in range(dh.lattice.nsc.prod())
    ]
)


# symmetrizing Hamiltonian and overlap matrix to make them hermitian
for i in range(dh.lattice.sc_off.shape[0]):
    j = dh.lattice.sc_index(-dh.lattice.sc_off[i])
    h1, h1d = hh[i], hh[j]
    hh[i], hh[j] = (h1 + h1d.T.conj()) / 2, (h1d + h1.T.conj()) / 2
    s1, s1d = ss[i], ss[j]
    ss[i], ss[j] = (s1 + s1d.T.conj()) / 2, (s1d + s1.T.conj()) / 2

# identifying TRS and TRB parts of the Hamiltonian
TAUY = np.kron(np.eye(NO), tau_y)
hTR = np.array([TAUY @ hh[i].conj() @ TAUY for i in range(dh.lattice.nsc.prod())])
hTRS = (hh + hTR) / 2
hTRB = (hh - hTR) / 2

# extracting the exchange field
traced = [spin_tracer(hTRB[i]) for i in range(dh.lattice.nsc.prod())]  # equation 77
XCF = np.array(
    [
        np.array([f["x"] for f in traced]),
        np.array([f["y"] for f in traced]),
        np.array([f["z"] for f in traced]),
    ]
)  # equation 77

# Check if exchange field has scalar part
max_xcfs = abs(np.array(np.array([f["c"] for f in traced]))).max()
if max_xcfs > 1e-12:
    warnings.warn(
        f"Exchange field has non negligible scalar part. Largest value is {max_xcfs}"
    )

times["H_and_XCF_time"] = timer()

In [ ]:
# for every site we have to store 3 Greens function (and the associated _tmp-s) in the 3 reference directions
for i, mag_ent in enumerate(magnetic_entities):
    parsed = parse_magnetic_entity(dh, **mag_ent)  # parse orbital indexes
    magnetic_entities[i]["orbital_indeces"] = parsed
    # calculate spin box indexes
    magnetic_entities[i]["spin_box_indeces"] = blow_up_orbindx(parsed)
    # calculate size for Greens function generation
    spin_box_shape = len(mag_ent["spin_box_indeces"])

    mag_ent["energies"] = []  # we will store the second order energy derivations here

    mag_ent["Gii"] = []  # Greens function
    mag_ent["Gii_tmp"] = []  # Greens function for parallelization
    # These will be the perturbed potentials from eq. 100
    mag_ent["Vu1"] = [list([]) for _ in range(len(ref_xcf_orientations))]
    mag_ent["Vu2"] = [list([]) for _ in range(len(ref_xcf_orientations))]
    for i in ref_xcf_orientations:
        # Greens functions for every quantization axis
        mag_ent["Gii"].append(
            np.zeros((eset, spin_box_shape, spin_box_shape), dtype="complex128")
        )
        mag_ent["Gii_tmp"].append(
            np.zeros((eset, spin_box_shape, spin_box_shape), dtype="complex128")
        )

# for every site we have to store 2x3 Greens function (and the associated _tmp-s)
# in the 3 reference directions, because G_ij and G_ji are both needed
for pair in pairs:
    # calculate size for Greens function generation
    spin_box_shape_i = len(magnetic_entities[pair["ai"]]["spin_box_indeces"])
    spin_box_shape_j = len(magnetic_entities[pair["aj"]]["spin_box_indeces"])

    pair["energies"] = []  # we will store the second order energy derivations here

    pair["Gij"] = []  # Greens function
    pair["Gji"] = []
    pair["Gij_tmp"] = []  # Greens function for parallelization
    pair["Gji_tmp"] = []
    for i in ref_xcf_orientations:
        # Greens functions for every quantization axis
        pair["Gij"].append(
            np.zeros((eset, spin_box_shape_i, spin_box_shape_j), dtype="complex128")
        )
        pair["Gij_tmp"].append(
            np.zeros((eset, spin_box_shape_i, spin_box_shape_j), dtype="complex128")
        )
        pair["Gji"].append(
            np.zeros((eset, spin_box_shape_j, spin_box_shape_i), dtype="complex128")
        )
        pair["Gji_tmp"].append(
            np.zeros((eset, spin_box_shape_j, spin_box_shape_i), dtype="complex128")
        )

times["site_and_pair_dictionaries_time"] = timer()

In [ ]:
kset = make_kset(dirs=kdirs, NUMK=kset)  # generate k space sampling
wkset = np.ones(len(kset)) / len(kset)  # generate weights for k points
kpcs = np.array_split(kset, size)  # split the k points based on MPI size
kpcs[root_node] = tqdm(kpcs[root_node], desc="k loop", file=stdout)

times["k_set_time"] = timer()

In [ ]:
# this will contain the three hamiltonians in the reference directions needed to calculate the energy variations upon rotation
hamiltonians = []

# iterate over the reference directions (quantization axes)
for i, orient in enumerate(ref_xcf_orientations):
    # obtain rotated exchange field
    R = RotMa2b(scf_xcf_orientation, orient["o"])
    rot_XCF = np.einsum("ij,jklm->iklm", R, XCF)
    rot_H_XCF = sum(
        [np.kron(rot_XCF[i], tau) for i, tau in enumerate([tau_x, tau_y, tau_z])]
    )
    rot_H_XCF_uc = rot_H_XCF[uc_in_sc_idx]

    # obtain total Hamiltonian with the rotated exchange field
    rot_H = (
        hTRS + rot_H_XCF
    )  # equation 76 #######################################################################################

    hamiltonians.append(
        dict(orient=orient["o"], H=rot_H)
    )  # store orientation and rotated Hamiltonian

    # these are the infinitezimal rotations (for now) perpendicular to the quantization axis
    for u in orient["vw"]:
        Tu = np.kron(np.eye(NO, dtype=int), tau_u(u))  # section 2.H

        Vu1 = 1j / 2 * commutator(rot_H_XCF_uc, Tu)  # equation 100
        Vu2 = 1 / 8 * commutator(commutator(Tu, rot_H_XCF_uc), Tu)  # equation 100

        for mag_ent in magnetic_entities:
            # fill up the perturbed potentials (for now) based on the on-site projections
            mag_ent["Vu1"][i].append(
                Vu1[:, mag_ent["spin_box_indeces"]][mag_ent["spin_box_indeces"], :]
            )
            mag_ent["Vu2"][i].append(
                Vu2[:, mag_ent["spin_box_indeces"]][mag_ent["spin_box_indeces"], :]
            )

times["reference_rotations_time"] = timer()

In [ ]:
if rank == root_node:
    print("Number of magnetic entities being calculated: ", len(magnetic_entities))
    print(
        "We have to calculate the Greens function for three reference direction and we are going to calculate 15 energy integrals per site."
    )
    print(f"The shape of the Hamiltonian and the Greens function is {NO}x{NO}.")
comm.Barrier()
# ----------------------------------------------------------------------

# make energy contour
# we are working in eV now  !
# and sisil shifts E_F to 0 !
cont = make_contour(emin=ebot, enum=eset, p=esetp)
eran = cont.ze

# ----------------------------------------------------------------------
# sampling the integrand on the contour and the BZ
for k in kpcs[rank]:
    wk = wkset[rank]  # weight of k point in BZ integral
    # iterate over reference directions
    for i, hamiltonian_orientation in enumerate(hamiltonians):
        # calculate Greens function
        H = hamiltonian_orientation["H"]
        HK, SK = hsk(H, ss, dh.sc_off, k)
        Gk = inv(SK * eran.reshape(eset, 1, 1) - HK)

        # solve Greens function sequentially for the energies, because of memory bound
        # Gk = np.zeros(shape=(eset, HK.shape[0], HK.shape[1]), dtype="complex128")
        # for j in range(eset):
        #    Gk[j] = inv(SK * eran[j] - HK)

        # store the Greens function slice of the magnetic entities (for now) based on the on-site projections
        for mag_ent in magnetic_entities:
            mag_ent["Gii_tmp"][i] += (
                Gk[:, mag_ent["spin_box_indeces"]][..., mag_ent["spin_box_indeces"]]
                * wk
            )

        for pair in pairs:
            # add phase shift based on the cell difference
            phase = np.exp(1j * 2 * np.pi * k @ pair["Ruc"].T)

            # get the pair orbital sizes from the magnetic entities
            ai = magnetic_entities[pair["ai"]]["spin_box_indeces"]
            aj = magnetic_entities[pair["aj"]]["spin_box_indeces"]

            # store the Greens function slice of the magnetic entities (for now) based on the on-site projections
            pair["Gij_tmp"][i] += Gk[:, ai][..., aj] * phase * wk
            pair["Gji_tmp"][i] += Gk[:, aj][..., ai] * phase * wk

# summ reduce partial results of mpi nodes
for i in range(len(hamiltonians)):
    for mag_ent in magnetic_entities:
        comm.Reduce(mag_ent["Gii_tmp"][i], mag_ent["Gii"][i], root=root_node)

    for pair in pairs:
        comm.Reduce(pair["Gij_tmp"][i], pair["Gij"][i], root=root_node)
        comm.Reduce(pair["Gji_tmp"][i], pair["Gji"][i], root=root_node)

times["green_function_inversion_time"] = timer()

In [ ]:
if rank == root_node:
    # iterate over the magnetic entities
    for tracker, mag_ent in enumerate(magnetic_entities):
        # iterate over the quantization axes
        for i, Gii in enumerate(mag_ent["Gii"]):
            storage = []
            # iterate over the first and second order local perturbations
            for Vu1, Vu2 in zip(mag_ent["Vu1"][i], mag_ent["Vu2"][i]):
                # The Szunyogh-Lichtenstein formula
                traced = np.trace((Vu2 @ Gii + 0.5 * Gii @ Vu1 @ Gii), axis1=1, axis2=2)
                # evaluation of the contour integral
                storage.append(np.trapz(-1 / np.pi * np.imag(traced * cont.we)))

            # fill up the magnetic entities dictionary with the energies
            magnetic_entities[tracker]["energies"].append(storage)

    # iterate over the pairs
    for tracker, pair in enumerate(pairs):
        # iterate over the quantization axes
        for i, (Gij, Gji) in enumerate(zip(pair["Gij"], pair["Gji"])):
            site_i = magnetic_entities[pair["ai"]]
            site_j = magnetic_entities[pair["aj"]]

            storage = []
            # iterate over the first order local perturbations in all possible orientations for the two sites
            for Vui in site_i["Vu1"][i]:
                for Vuj in site_j["Vu1"][i]:
                    # The Szunyogh-Lichtenstein formula
                    traced = np.trace((Vui @ Gij @ Vuj @ Gji), axis1=1, axis2=2)
                    # evaluation of the contour integral
                    storage.append(np.trapz(-1 / np.pi * np.imag(traced * cont.we)))
            # fill up the pairs dictionary with the energies
            pairs[tracker]["energies"].append(storage)

    times["end_time"] = timer()
    print_output(simulation_parameters, magnetic_entities, pairs, dh, times)

In [ ]:
##################################################################### GROGU OUTPUT #############################################################################
================================================================================================================================================================
Input file: 
Not yet specified.
Number of nodes in the parallel cluster:  1
================================================================================================================================================================
Cell [Ang]: 
[[ 6.47        0.          0.        ]
 [-3.235       5.60318436  0.        ]
 [ 0.          0.         29.999449  ]]
================================================================================================================================================================
DFT axis: 
[0 0 1]
Quantization axis and perpendicular rotation directions:
[1 0 0]  --»  [array([0, 1, 0]), array([0, 0, 1])]
[0 1 0]  --»  [array([1, 0, 0]), array([0, 0, 1])]
[0 0 1]  --»  [array([1, 0, 0]), array([0, 1, 0])]
================================================================================================================================================================
number of k points:  4
k point directions:  xy
================================================================================================================================================================
Parameters for the contour integral:
Ebot:  -30
Eset:  100
Esetp:  10000
================================================================================================================================================================
Atomic informations: 
----------------------------------------------------------------------------------------------------------------------------------------------------------------
[atom index]Element(orbitals)        x [Ang]        y [Ang]        z [Ang]        Sx        Sy        Sz        Q        Lx        Ly        Lz        Jx        Jy        Jz
----------------------------------------------------------------------------------------------------------------------------------------------------------------
[0]Cr(2)        0.025224941687312104        -0.014371429816522993        -0.020792425897793128

[1]Cr(2)        3.2508367285399955        1.8478445793345957        -0.02082986959108256

[2]Br(2)        2.1053343349045215        0.10721337338160676        -1.471910834765145

================================================================================================================================================================
Exchange [meV]
----------------------------------------------------------------------------------------------------------------------------------------------------------------
Magnetic entity1        Magnetic entity2       [i  j  k]       d [Ang]
----------------------------------------------------------------------------------------------------------------------------------------------------------------
[0]Cr(2)        [1]Cr(2)             [0 0 0]    d [Ang] Not yet.
Isotropic:  15.91078131425419
DMI:  [-3.16312278e-05  1.94021443e-05 -1.65972633e-04]
Symmetric-anisotropy:  [-0.03896181 -0.01392426 -0.07639227  0.05293223 -0.08712209]
Energies for debugging: 
array([[ 1.58968571e-02,  8.70904601e-05,  8.71537225e-05,
         1.59636674e-02],
       [ 1.58999738e-02, -5.29322330e-05, -5.28934287e-05,
         1.58718195e-02],
       [ 1.59589510e-02,  7.62263019e-05,  7.65582472e-05,
         1.58707914e-02]])
J_ii for debugging: (check if this is the same as in calculate_exchange_tensor)
array([0.01587182, 0.01595895, 0.01589686])
Test J_xx = E(y,z) = E(z,y)
0.015871819503030533 0.015870791381430095

[0]Cr(2)        [2]Br(2)             [0 0 0]    d [Ang] Not yet.
Isotropic:  0.14694676346924165
DMI:  [ 8.01967166e-05  8.29086493e-04 -9.27235617e-05]
Symmetric-anisotropy:  [ 2.66339812e-05 -4.77282294e-06 -6.60708923e-06  8.03002228e-04
 -2.98623982e-06]
Energies for debugging: 
array([[ 1.46941991e-04,  8.31829565e-08, -7.72104768e-08,
         1.46924902e-04],
       [ 1.46982775e-04, -8.03002228e-07,  8.55170759e-07,
         1.46973397e-04],
       [ 1.46942514e-04, -8.61164724e-08,  9.93306509e-08,
         1.46901824e-04]])
J_ii for debugging: (check if this is the same as in calculate_exchange_tensor)
array([0.00014697, 0.00014694, 0.00014694])
Test J_xx = E(y,z) = E(z,y)
0.00014697339745047312 0.00014690182371456808

[1]Cr(2)        [2]Br(2)             [0 0 0]    d [Ang] Not yet.
Isotropic:  0.146966596490555
DMI:  [ 7.83469069e-04 -3.25183011e-04  9.29353203e-05]
Symmetric-anisotropy:  [-1.73027923e-05  1.26068464e-05 -2.08606748e-05 -2.97793770e-04
  3.14336799e-07]
Energies for debugging: 
array([[ 1.46979203e-04,  7.83154732e-07, -7.83783406e-07,
         1.46971292e-04],
       [ 1.46912608e-04,  2.97793770e-07, -3.52572253e-07,
         1.46949294e-04],
       [ 1.46905570e-04,  1.13795995e-07, -7.20746454e-08,
         1.46914411e-04]])
J_ii for debugging: (check if this is the same as in calculate_exchange_tensor)
array([0.00014695, 0.00014691, 0.00014698])
Test J_xx = E(y,z) = E(z,y)
0.00014694929369829223 0.00014691441062702917

[0]Cr(2)        [1]Cr(2)             [1 0 0]    d [Ang] Not yet.
Isotropic:  0.09111814992141927
DMI:  [0.03377305 0.0340363  0.00964244]
Symmetric-anisotropy:  [-0.00291957  0.0031014  -0.0021492   0.03416682  0.0051237 ]
Energies for debugging: 
array([[ 9.42195473e-05,  2.86493440e-05, -3.88967487e-05,
         9.09363256e-05],
       [ 9.41093226e-05, -3.41668178e-05,  3.39057913e-05,
         8.81985768e-05],
       [ 9.14933866e-05,  1.17916416e-05, -7.49323868e-06,
         8.86473282e-05]])
J_ii for debugging: (check if this is the same as in calculate_exchange_tensor)
array([8.81985768e-05, 9.14933866e-05, 9.42195473e-05])
Test J_xx = E(y,z) = E(z,y)
8.819857682132204e-05 8.8647328224418e-05

[0]Cr(2)        [2]Br(2)             [1 0 0]    d [Ang] Not yet.
Isotropic:  0.00023346314999400802
DMI:  [-0.0002294  -0.0002349  -0.00020879]
Symmetric-anisotropy:  [-1.12556482e-05  1.43988058e-05 -1.55475448e-06 -2.34959571e-04
  6.19663196e-06]
Energies for debugging: 
array([[ 2.47861956e-07, -2.35597865e-07,  2.23204601e-07,
         2.30319992e-07],
       [ 2.10261125e-07,  2.34959571e-07, -2.34837442e-07,
         2.22207502e-07],
       [ 2.12323581e-07, -2.07238961e-07,  2.10348470e-07,
         2.07858965e-07]])
J_ii for debugging: (check if this is the same as in calculate_exchange_tensor)
array([2.22207502e-07, 2.12323581e-07, 2.47861956e-07])
Test J_xx = E(y,z) = E(z,y)
2.2220750178916023e-07 2.078589648170586e-07

[0]Cr(2)        [1]Cr(2)             [-1  0  0]    d [Ang] Not yet.
Isotropic:  0.09111258017019819
DMI:  [-0.03378783 -0.03403353 -0.0096277 ]
Symmetric-anisotropy:  [-0.00291741  0.00310155 -0.00214665 -0.03390027  0.00512057]
Energies for debugging: 
array([[ 9.42141309e-05, -3.89083994e-05,  2.86672518e-05,
         9.09284386e-05],
       [ 9.41042657e-05,  3.39002650e-05, -3.41667971e-05,
         8.81951711e-05],
       [ 9.14629700e-05, -7.48105019e-06,  1.17743519e-05,
         8.86174723e-05]])
J_ii for debugging: (check if this is the same as in calculate_exchange_tensor)
array([8.81951711e-05, 9.14629700e-05, 9.42141309e-05])
Test J_xx = E(y,z) = E(z,y)
8.819517110814147e-05 8.861747229207156e-05

[0]Cr(2)        [2]Br(2)             [-1  0  0]    d [Ang] Not yet.
Isotropic:  0.0002516119318884681
DMI:  [0.0002271  0.00022722 0.00023639]
Symmetric-anisotropy:  [ 8.12786238e-06 -1.33724299e-05  2.28353801e-06  2.31211900e-04
 -2.16488405e-06]
Energies for debugging: 
array([[ 2.38239502e-07,  2.29269073e-07, -2.24939305e-07,
         2.56856499e-07],
       [ 2.77408158e-07, -2.31211900e-07,  2.23219979e-07,
         2.59739794e-07],
       [ 2.73816864e-07,  2.34111415e-07, -2.38678491e-07,
         2.71887108e-07]])
J_ii for debugging: (check if this is the same as in calculate_exchange_tensor)
array([2.59739794e-07, 2.73816864e-07, 2.38239502e-07])
Test J_xx = E(y,z) = E(z,y)
2.5973979426862243e-07 2.718871078150382e-07

[0]Cr(2)        [1]Cr(2)             [0 1 0]    d [Ang] Not yet.
Isotropic:  -0.13657014924460614
DMI:  [ 0.00026859 -0.00029338 -0.0001818 ]
Symmetric-anisotropy:  [-0.00104734  0.00154555 -0.00046486 -0.00072287  0.00087507]
Energies for debugging: 
array([[-1.35024601e-04, -6.06475771e-07, -1.14365755e-06,
        -1.37068359e-04],
       [-1.34947686e-04,  7.22871593e-07,  1.36112752e-07,
        -1.37617487e-04],
       [-1.36691877e-04,  2.83065496e-07,  6.46663000e-07,
        -1.37228934e-04]])
J_ii for debugging: (check if this is the same as in calculate_exchange_tensor)
array([-0.00013762, -0.00013669, -0.00013502])
Test J_xx = E(y,z) = E(z,y)
-0.00013761748740593208 -0.00013722893403347796

[0]Cr(2)        [2]Br(2)             [0 1 0]    d [Ang] Not yet.
Isotropic:  -0.00010028627777987032
DMI:  [-8.54009417e-05 -1.21477411e-04 -8.32475011e-05]
Symmetric-anisotropy:  [ 1.89621993e-05 -7.40845210e-06  6.91965022e-07 -1.13803644e-04
 -7.00808812e-06]
Energies for debugging: 
array([[-1.07694730e-07, -7.83928536e-08,  9.24090298e-08,
        -1.11840025e-07],
       [-8.13196124e-08,  1.13803644e-07, -1.29151178e-07,
        -8.13240785e-08],
       [-1.76542958e-07, -8.39394661e-08,  8.25555360e-08,
        -1.76140161e-07]])
J_ii for debugging: (check if this is the same as in calculate_exchange_tensor)
array([-8.13240785e-08, -1.76542958e-07, -1.07694730e-07])
Test J_xx = E(y,z) = E(z,y)
-8.132407846090182e-08 -1.7614016112304844e-07

[0]Cr(2)        [1]Cr(2)             [0 1 0]    d [Ang] Not yet.
Isotropic:  -0.13657014924460614
DMI:  [ 0.00026859 -0.00029338 -0.0001818 ]
Symmetric-anisotropy:  [-0.00104734  0.00154555 -0.00046486 -0.00072287  0.00087507]
Energies for debugging: 
array([[-1.35024601e-04, -6.06475771e-07, -1.14365755e-06,
        -1.37068359e-04],
       [-1.34947686e-04,  7.22871593e-07,  1.36112752e-07,
        -1.37617487e-04],
       [-1.36691877e-04,  2.83065496e-07,  6.46663000e-07,
        -1.37228934e-04]])
J_ii for debugging: (check if this is the same as in calculate_exchange_tensor)
array([-0.00013762, -0.00013669, -0.00013502])
Test J_xx = E(y,z) = E(z,y)
-0.00013761748740593208 -0.00013722893403347796

[0]Cr(2)        [2]Br(2)             [0 1 0]    d [Ang] Not yet.
Isotropic:  -0.00010028627777987032
DMI:  [-8.54009417e-05 -1.21477411e-04 -8.32475011e-05]
Symmetric-anisotropy:  [ 1.89621993e-05 -7.40845210e-06  6.91965022e-07 -1.13803644e-04
 -7.00808812e-06]
Energies for debugging: 
array([[-1.07694730e-07, -7.83928536e-08,  9.24090298e-08,
        -1.11840025e-07],
       [-8.13196124e-08,  1.13803644e-07, -1.29151178e-07,
        -8.13240785e-08],
       [-1.76542958e-07, -8.39394661e-08,  8.25555360e-08,
        -1.76140161e-07]])
J_ii for debugging: (check if this is the same as in calculate_exchange_tensor)
array([-8.13240785e-08, -1.76542958e-07, -1.07694730e-07])
Test J_xx = E(y,z) = E(z,y)
-8.132407846090182e-08 -1.7614016112304844e-07

================================================================================================================================================================
Runtime information: 
Total runtime: 16.641370917 s
----------------------------------------------------------------------------------------------------------------------------------------------------------------
Initial setup: 0.07859033299999996 s
Hamiltonian conversion and XC field extraction: 0.683 s
Pair and site datastructure creatrions: 0.012 s
k set cration and distribution: 0.023 s
Rotating XC potential: 0.243 s
Greens function inversion: 15.524 s
Calculate energies and magnetic components: 0.078 s

In [ ]:
========================================
 
Atom Angstrom
# Label,        x           y           z          Sx           Sy           Sz         #Q           Lx           Ly           Lz           Jx           Jy           Jz
--------------------------------------------------------------------------------------------------------------------------------------------------------------------------
Te1         1.8955      1.0943      13.1698     -0.0000     0.0000      -0.1543    # 5.9345       -0.0000      0.0000       -0.0537      -0.0000      0.0000       -0.2080   
Te2         1.8955      1.0943      7.4002      0.0000      -0.0000     -0.1543    # 5.9345       0.0000       -0.0000      -0.0537      0.0000       -0.0000      -0.2080   
Ge3         -0.0000     2.1887      10.2850     0.0000      0.0000      -0.1605    # 3.1927       -0.0000      0.0000       0.0012       0.0000       0.0000       -0.1593   
Fe4         -0.0000     0.0000      11.6576     0.0001      -0.0001     2.0466     # 8.3044       0.0000       -0.0000      0.1606       0.0001       -0.0001      2.2072    
Fe5         -0.0000     0.0000      8.9124      -0.0001     0.0001      2.0466     # 8.3044       -0.0000      0.0000       0.1606       -0.0001      0.0001       2.2072    
Fe6         1.8955      1.0944      10.2850     0.0000      0.0000      1.5824     # 8.3296       -0.0000      -0.0000      0.0520       -0.0000      0.0000       1.6344    
==================================================================================================================================
 
Exchange meV
--------------------------------------------------------------------------------
# at1     at2   i  j  k    #    d (Ang)
--------------------------------------------------------------------------------
Fe4     Fe5     0  0  0    #    2.7452
Isotropic -82.0854
DMI 0.12557 -0.00082199  6.9668e-08
Symmetric-anisotropy -0.60237    -0.83842 -0.00032278 -1.2166e-05 -3.3923e-05
--------------------------------------------------------------------------------
Fe4     Fe6     0  0  0    #    2.5835
Isotropic -41.9627
DMI 1.1205     -1.9532   0.0018386
Symmetric-anisotropy 0.26007 -0.00013243     0.12977   -0.069979   -0.042066
--------------------------------------------------------------------------------


In [ ]:
import sisl.viz

dh.geometry.tile(2, 1).plot(axes="xy")

In [ ]:
import matplotlib.pyplot as plt

coords = dh.xyz[-3:]


plt.figure(figsize=(15, 5))
plt.subplot(131)
plt.scatter(coords[:, 0], coords[:, 2], color=["r", "g", "b"])
plt.xlabel("x")
plt.ylabel("z")
plt.subplot(132)
plt.scatter(coords[:, 1], coords[:, 2], color=["r", "g", "b"])
plt.xlabel("y")
plt.ylabel("z")
plt.subplot(133)
plt.scatter(coords[:, 0], coords[:, 1], color=["r", "g", "b"])
plt.xlabel("x")
plt.ylabel("y")
print("xyz[-3:]: red, green, blue")